# Intro. to Snorkel: Extracting Spouse Relations from the News

## Part III: Training an End Extraction Model

In this final section of the tutorial, we'll use the noisy training labels we generated in the last tutorial part to train our end extraction model.

For this tutorial, we will be training a Bi-LSTM, a state-of-the-art deep neural network implemented in [TensorFlow](https://www.tensorflow.org/).

In [1]:
%load_ext autoreload
%autoreload 2
%matplotlib inline
import os

# TO USE A DATABASE OTHER THAN SQLITE, USE THIS LINE
# Note that this is necessary for parallel execution amongst other things...
# os.environ['SNORKELDB'] = 'postgres:///snorkel-intro'

from snorkel import SnorkelSession
session = SnorkelSession()

We repeat our definition of the `Spouse` `Candidate` subclass:

In [2]:
from snorkel.models import candidate_subclass

Spouse = candidate_subclass('Spouse', ['person1', 'person2'])

We reload the probabilistic training labels:

In [3]:
from snorkel.annotations import load_marginals

train_marginals = load_marginals(session, split=0)

IndexError: list index out of range

We also reload the candidates:

In [4]:
train_cands = session.query(Spouse).filter(Spouse.split == 0).order_by(Spouse.id).all()
dev_cands   = session.query(Spouse).filter(Spouse.split == 1).order_by(Spouse.id).all()
test_cands  = session.query(Spouse).filter(Spouse.split == 2).order_by(Spouse.id).all()

In [5]:
for c in train_cands:
    if not in c.get_parent().text:
        print c
        print c.get_parent().text
        print

Spouse(Span("Sandringham", sentence=21095, chars=[28,38], words=[6,6]), Span("Granville Roberts", sentence=21095, chars=[70,86], words=[12,13]))
The source of the news from Sandringham came from a journalist called Granville Roberts, who worked on the East African Standard and was covering the royal visit.   

Spouse(Span("Twitter", sentence=24262, chars=[235,241], words=[46,46]), Span("Kerry", sentence=24262, chars=[441,445], words=[86,86]))
Special guest: Ariana Grande arrived to join Coldplay for a duet      Chic: The One Last Time singer looked stylish in a black and white striped jumpsuit with a plunging front and cut-outs      Grateful: The Scream Queens star took to Twitter following the performance to gush: 'thank you @coldplay [heart emoji] it was an honor to say the least #GlobalCitizenFestival'   Actress Freida Pinto was also spotted walking the carpet, along with Kerry, as she arrived at the star-studded festival.    

Spouse(Span("Chic", sentence=24262, chars=[70,73], word

Spouse(Span("Emma", sentence=52073, chars=[12,15], words=[3,3]), Span("Aric", sentence=52073, chars=[90,93], words=[19,19]))
Cast party: Emma was joined by other stars from the show as she partied the night away    Aric and Emma celebrated their historic win on the dance competition into the early hours of Tuesday according to reports.   

Spouse(Span("Emma", sentence=52073, chars=[12,15], words=[3,3]), Span("Emma", sentence=52073, chars=[99,102], words=[21,21]))
Cast party: Emma was joined by other stars from the show as she partied the night away    Aric and Emma celebrated their historic win on the dance competition into the early hours of Tuesday according to reports.   

Spouse(Span("Adi", sentence=48602, chars=[28,30], words=[4,4]), Span("Bruno Mars'", sentence=48602, chars=[137,147], words=[28,30]))
The ceremony concluded with Adi, heir to Israeli food importing company Neto ME Holdings, Ltd., stepping on a glass to seal the union as Bruno Mars' Marry Me played.   

Spouse(Span(

Tuesdays with Morrie   Written by Mitch Albom in 1997, Tuesdays with Morrie documents the weekly meetings between Albom and his former Brandeis Professor, Morrie Schwartz.

Spouse(Span("Morrie   ", sentence=38410, chars=[14,22], words=[2,3]), Span("Albom", sentence=38410, chars=[114,118], words=[19,19]))
Tuesdays with Morrie   Written by Mitch Albom in 1997, Tuesdays with Morrie documents the weekly meetings between Albom and his former Brandeis Professor, Morrie Schwartz.

Spouse(Span("Morrie   ", sentence=38410, chars=[14,22], words=[2,3]), Span("Morrie Schwartz", sentence=38410, chars=[155,169], words=[26,27]))
Tuesdays with Morrie   Written by Mitch Albom in 1997, Tuesdays with Morrie documents the weekly meetings between Albom and his former Brandeis Professor, Morrie Schwartz.

Spouse(Span("Mitch Albom", sentence=38410, chars=[34,44], words=[6,7]), Span("Morrie", sentence=38410, chars=[69,74], words=[13,13]))
Tuesdays with Morrie   Written by Mitch Albom in 1997, Tuesdays with Mo


Spouse(Span("Schwartz", sentence=38411, chars=[22,29], words=[4,4]), Span("Lou Gehrig's", sentence=38411, chars=[61,72], words=[11,13]))
The story begins when Schwartz, recently diagnosed with ALS (Lou Gehrig's Disease), receives a surprise visit from his former student, Albom.

Spouse(Span("Schwartz", sentence=38411, chars=[22,29], words=[4,4]), Span("Albom", sentence=38411, chars=[135,139], words=[26,26]))
The story begins when Schwartz, recently diagnosed with ALS (Lou Gehrig's Disease), receives a surprise visit from his former student, Albom.

Spouse(Span("Lou Gehrig's", sentence=38411, chars=[61,72], words=[11,13]), Span("Albom", sentence=38411, chars=[135,139], words=[26,26]))
The story begins when Schwartz, recently diagnosed with ALS (Lou Gehrig's Disease), receives a surprise visit from his former student, Albom.

Spouse(Span("Nolan", sentence=13355, chars=[0,4], words=[0,0]), Span("Leonardo DiCaprio", sentence=13355, chars=[75,91], words=[15,16]))
Nolan was preparing to mak

Spouse(Span("Mario", sentence=64043, chars=[0,4], words=[0,0]), Span("Mario", sentence=64043, chars=[33,37], words=[8,8]))
Mario 64: "Peach decides to give Mario one last chance to get it right.

Spouse(Span("Sharon Gauci", sentence=34812, chars=[46,57], words=[9,10]), Span("Con Gerkis", sentence=34812, chars=[75,84], words=[14,15]))
… GM director of global color and trim design Sharon Gauci and her husband Con Gerkis have owned three 1969 Chevrolet Camaros. "

Spouse(Span("Maddie", sentence=68973, chars=[184,189], words=[31,31]), Span("Dave", sentence=68973, chars=[321,324], words=[53,53]))
Since then, they have awarded more than $153 million in grants toward increased community lifesaving, shelter medicine education, and pet adoptions across the U.S. The Duffields named Maddie's Fund after their Miniature Schnauzer Maddie, who always made them laugh and comforted them during stressful business times when Dave was launching a start-up company.

Spouse(Span("Duffields", sentence=68973,

...

Spouse(Span("Greste", sentence=68659, chars=[13,18], words=[3,3]), Span("Abded Fattah al-Sisi", sentence=68659, chars=[51,70], words=[8,12]))
an elated Mr Greste exclaimed   Egyptian president Abded Fattah al-Sisi has pardoned 100 prisoners  It's still unknown if Mr Greste is one of those officially pardoned   He escaped more prison time due to his February deportation from Egypt   The emotional moment that Australian journalist Peter Greste discovered that his colleagues had been freed from prison in Egypt has been captured on TV.   

Spouse(Span("Abded Fattah al-Sisi", sentence=68659, chars=[51,70], words=[8,12]), Span("Mr Greste", sentence=68659, chars=[122,130], words=[23,24]))
an elated Mr Greste exclaimed   Egyptian president Abded Fattah al-Sisi has pardoned 100 prisoners  It's still unknown if Mr Greste is one of those officially pardoned   He escaped more prison time due to his February deportation from Egypt   The emotional moment that Australian journalist Peter Greste disco

Spouse(Span("William Tyrrell", sentence=29098, chars=[136,150], words=[21,22]), Span("William Tyrrell", sentence=29098, chars=[380,394], words=[64,65]))
Today marks the one year anniversary of missing toddler William Tyrrell  Australians across the country are marching to raise awareness William Tyrrell was abducted from Kendall one year ago on Saturday    He would have turned four in June   Thousands of Australians across the country came together today at marches and community events to mark one year to the day since toddler William Tyrrell vanished without trace.   

Spouse(Span("William Tyrrell", sentence=29098, chars=[56,70], words=[9,10]), Span("William Tyrrell", sentence=29098, chars=[380,394], words=[64,65]))
Today marks the one year anniversary of missing toddler William Tyrrell  Australians across the country are marching to raise awareness William Tyrrell was abducted from Kendall one year ago on Saturday    He would have turned four in June   Thousands of Australians across

Experts Claudia Paz, Carlos Beristain and Angela Buitrago of the Inter-American Commission on Human Rights present the first conclusions of the investigation.

Spouse(Span("Claudia Paz", sentence=16792, chars=[8,18], words=[1,2]), Span("Carlos Beristain", sentence=16792, chars=[21,36], words=[4,5]))
Experts Claudia Paz, Carlos Beristain and Angela Buitrago of the Inter-American Commission on Human Rights present the first conclusions of the investigation.

Spouse(Span("Kim Kardashian", sentence=46203, chars=[175,188], words=[33,34]), Span("Joe Jonas", sentence=46203, chars=[313,321], words=[60,61]))
Superstar: Bella also draped a leather jacket over her shoulder, complete with colourful stars all over     Flawless: As busy Bella made her way to dinner with her sister and Kim Kardashian, hosted by Carine Roitfeld, she looked as fresh-faced as ever despite her busy schedule      Casual gent: Gigi's boyfriend Joe Jonas joined the girls later in the evening as they went along to Kylie Jenn

Spouse(Span("Simon Cowell", sentence=24459, chars=[107,118], words=[17,18]), Span("Chloe", sentence=24459, chars=[156,160], words=[26,26]))
Online commentary: Tweeters have suggested the market trader lacks 'cultural appreciation'      Impressed: Simon Cowell and his judging panel were wowed by Chloe's rendition of Katy B's Crying

Spouse(Span("Jane Lang", sentence=8500, chars=[0,8], words=[0,1]), Span("Salem", sentence=8500, chars=[24,28], words=[5,5]))
Jane Lang, an undecided Salem voter leaning towards Sanders, said that to her, it feels like 2008 all over again -- Clinton is losing to a truth-telling progressive champion who knows exactly what Democrats want.   

Spouse(Span("Jane Lang", sentence=8500, chars=[0,8], words=[0,1]), Span("Clinton", sentence=8500, chars=[116,122], words=[24,24]))
Jane Lang, an undecided Salem voter leaning towards Sanders, said that to her, it feels like 2008 all over again -- Clinton is losing to a truth-telling progressive champion who knows exactly w

Spouse(Span("Jennifer McBride", sentence=30143, chars=[180,195], words=[37,38]), Span("Kelly", sentence=30143, chars=[206,210], words=[42,42]))
There is clear evidence of that in the reconciliation with her children and the day-in and day-out of how she treats prison staff and her fellow inmates,' Kelly's former professor Jennifer McBride said    'Kelly has had really a complete transformation.

Spouse(Span("Kelly", sentence=30143, chars=[155,159], words=[33,33]), Span("Jennifer McBride", sentence=30143, chars=[180,195], words=[37,38]))
There is clear evidence of that in the reconciliation with her children and the day-in and day-out of how she treats prison staff and her fellow inmates,' Kelly's former professor Jennifer McBride said    'Kelly has had really a complete transformation.

Spouse(Span("Kelly", sentence=30143, chars=[155,159], words=[33,33]), Span("Kelly", sentence=30143, chars=[206,210], words=[42,42]))
There is clear evidence of that in the reconciliation with her childr

Finally, we load gold labels for evaluation:

In [10]:
from snorkel.annotations import load_gold_labels

L_gold_dev  = load_gold_labels(session, annotator_name='gold', split=1)
L_gold_test = load_gold_labels(session, annotator_name='gold', split=2)

Now we can setup our discriminative model. Here we specify the model and learning hyperparameters.

They can also be set automatically using a search based on the dev set with a [GridSearch](https://github.com/HazyResearch/snorkel/blob/master/snorkel/learning/utils.py) object.

In [16]:
from snorkel.learning.disc_models.rnn import reRNN

train_kwargs = {
    'lr':         0.01,
    'dim':        50,
    'n_epochs':   10,
    'dropout':    0.25,
    'print_freq': 1,
    'max_sentence_length': 100
}

lstm = reRNN(seed=1701, n_threads=None)
lstm.train(train_cands, train_marginals, X_dev=dev_cands, Y_dev=L_gold_dev, **train_kwargs)

[reRNN] Training model
[reRNN] n_train=17205  #epochs=10  batch size=256
[reRNN] Epoch 0 (23.43s)	Average loss=0.566997	Dev F1=34.46
[reRNN] Epoch 1 (48.20s)	Average loss=0.535070	Dev F1=36.13
[reRNN] Epoch 2 (73.24s)	Average loss=0.533329	Dev F1=35.49
[reRNN] Epoch 3 (98.04s)	Average loss=0.532918	Dev F1=36.92
[reRNN] Epoch 4 (123.41s)	Average loss=0.532681	Dev F1=35.93
[reRNN] Epoch 5 (148.55s)	Average loss=0.532237	Dev F1=33.81
[reRNN] Epoch 6 (174.32s)	Average loss=0.531906	Dev F1=38.29
[reRNN] Epoch 7 (199.92s)	Average loss=0.531722	Dev F1=38.26
[reRNN] Epoch 8 (224.76s)	Average loss=0.531367	Dev F1=38.54
[reRNN] Model saved as <reRNN>
[reRNN] Epoch 9 (251.51s)	Average loss=0.531073	Dev F1=39.50
[reRNN] Model saved as <reRNN>
[reRNN] Training done (254.57s)
[reRNN] Loaded model <reRNN>


Now, we get the precision, recall, and F1 score from the discriminative model:

In [17]:
p, r, f1 = lstm.score(test_cands, L_gold_test)
print("Prec: {0:.3f}, Recall: {1:.3f}, F1 Score: {2:.3f}".format(p, r, f1))

Prec: 0.333, Recall: 0.692, F1 Score: 0.450


We can also get the candidates returned in sets (true positives, false positives, true negatives, false negatives) as well as a more detailed score report:

In [18]:
tp, fp, tn, fn = lstm.error_analysis(session, test_cands, L_gold_test)

Scores (Un-adjusted)
Pos. class accuracy: 0.692
Neg. class accuracy: 0.875
Precision            0.333
Recall               0.692
F1                   0.45
----------------------------------------
TP: 155 | FP: 310 | TN: 2163 | FN: 69



Note that if this is the final test set that you will be reporting final numbers on, to avoid biasing results you should not inspect results.  However you can run the model on your _development set_ and, as we did in the previous part with the generative labeling function model, inspect examples to do error analysis.

You can also improve performance substantially by increasing the number of training epochs!

Finally, we can save the predictions of the model on the test set back to the database. (This also works for other candidate sets, such as unlabeled candidates.)

In [19]:
lstm.save_marginals(session, test_cands)

Saved 2697 marginals


##### More importantly, you completed the introduction to Snorkel! Give yourself a pat on the back!